<a href="https://colab.research.google.com/github/ericmuckley/code/blob/master/milk_spectral_analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Import libraries that we need

In [0]:
# for importing / exporting files and creating DataFrames (tables)
import pandas as pd
# for dealing with multi-dimensional arrays
import numpy as np
# for smoothing and fitting spectra
from scipy import signal
from scipy.interpolate import splrep, splev
# for creating interactive plots
import itertools 
import bokeh
from bokeh.plotting import figure
from bokeh.io import output_notebook, show
from bokeh.palettes import Dark2_8 as palette

### Create custom functions for making interactive plots using Bokeh

In [0]:
def setup_fig(title='Title', xlabel='X', ylabel='Y', fontsize=12):
    """
    Create interactive Bokeh plot.
    """
    # create the figure
    p = figure(width=600, height=400,
               title=title,
               x_axis_label=xlabel,
               y_axis_label=ylabel,
               tools="pan,wheel_zoom,box_zoom,reset")
    # adjust properties of the figure to make it look good
    p.toolbar.logo = None
    fs = str(int(fontsize))+'pt'
    p.title.text_font_size = fs
    p.xaxis.axis_label_text_font_size = fs
    p.yaxis.axis_label_text_font_size = fs
    p.xaxis.major_label_text_font_size = fs
    p.yaxis.major_label_text_font_size = fs
    p.xaxis.axis_label_text_font_style = "normal"
    p.yaxis.axis_label_text_font_style = "normal"
    return p

def plot_line(df, title='Title', xlabel='X', ylabel='Y', fontsize=12):
    """
    Create interactive Bokeh line plot. Input df should be Pandas Dataframe,
    where the first column is x-values and following columns are y-values.
    """
    p = setup_fig(title=title, xlabel=xlabel, ylabel=ylabel, fontsize=fontsize)
    colors = itertools.cycle(palette)
    # loop over each column in the data and add to plot
    for col, color in zip(range(1, len(df.columns)), colors):
        p.line(df[df.columns[0]],
               df[df.columns[col]],
               line_color=color,
               line_width=4, legend=df.columns[col], alpha=0.6,
               muted_color=color, muted_alpha=0.2)
    p.legend.click_policy = "mute"
    # show the plot after this function using show(p)
    output_notebook()
    return p

### Import data files from Github and plot raw data

In [0]:
# list of files to import
file_list = ['milk__FTIR.csv', 'milk__RAMAN.csv', 'milk__UVVIS.csv']

# Github URL where files are being stored
url = 'https://raw.githubusercontent.com/ericmuckley/datasets/master/'

# create empty dictionary to hold raw dataframes
raw_dfs = {}

# loop over each file to import it
for filename in file_list:

    # read the file from the URL as a csv file into a Pandas DataFrame
    df = pd.read_csv(url + filename)

    # sort low to high by wavenumber. this is required for spline smoothing
    df.sort_values(by=df.columns[0], inplace=True)

    # get the measurement type from the filename
    measurement_type = filename.split('__')[1].split('.csv')[0].lower()

    # save the dataframe to the dictionary
    raw_dfs[measurement_type] = df

    # display information about each file and plot all spectra
    print('\n\n------------- ' + measurement_type.upper() + ' --------------')
    print('rows: %i, columns: %i' %(df.shape[0], df.shape[1]))
    # show the first few rows of the file
    print(df.head())
    #plot the data using our custom plot_line function
    p = plot_line(df, title=measurement_type.upper(),
                  xlabel=df.columns[0], ylabel='Intensity')
    show(p)



------------- FTIR --------------
rows: 1867, columns: 7
              w     day1     day2     day3     day4     day5     day6
1866  399.20229  0.24052  0.26080  0.24382  0.26968  0.31730  0.27146
1865  401.13080  0.24032  0.26042  0.24278  0.27428  0.32127  0.26916
1864  403.05932  0.23823  0.25808  0.24205  0.27714  0.32322  0.26622
1863  404.98783  0.23838  0.25581  0.24218  0.27599  0.32274  0.26462
1862  406.91634  0.24189  0.25584  0.24291  0.27213  0.32054  0.26472




------------- RAMAN --------------
rows: 5220, columns: 7
               w         day1  ...         day5         day6
5219   99.417503  1956.272949  ...  2055.408447  2694.281250
5218  100.552315  2027.160278  ...  2216.655518  2672.766602
5217  101.686905  2009.920288  ...  2256.752686  2838.571777
5216  102.821281  2096.275146  ...  2418.100586  2975.784668
5215  103.955437  2178.253662  ...  2400.929199  2980.768066

[5 rows x 7 columns]




------------- UVVIS --------------
rows: 1801, columns: 7
        w      day1      day2      day3      day4      day5      day6
1800  200  1.525290  1.411493  1.225504  1.455335  1.944736  1.246034
1799  201  1.596420  1.367719  1.194246  1.530849  1.980900  1.211463
1798  202  1.604842  1.398759  1.259107  1.421070  2.039033  1.289129
1797  203  1.612978  1.320230  1.138830  1.410097  1.978017  1.115122
1796  204  1.595931  1.239846  1.121634  1.387371  1.907074  1.261404


### Resample and normalize each spectrum
To use multiple spectra as inputs for a model,
the number of points in each type of spectrum should be the same.

Here we fit each spectrum to a spline and resample it into
a specified number of points **new_length**. Then we plot the original data
and the new resampled spectra to make sure that the resampling did not
change the shape of the spectrum.

For using the spectra in PCA or machine learning models, they should be
normalized first. The easiest way to do this is subtract each spectrum
by its minimum value and divide by the maximum value, so the min-max
scale goes from 0-1. This is done by the **normalize_df** function.

In [0]:
def arr_resample(arr, new_len=100, new_xlims=None, vec_scale='lin', k=3, s=0):
    '''
    Resamples (stetches/compresses) a 2D array by using a spline fit.
    Array should be shape [[x1, y1, ...ym], ...[xn, yn, ...yn]] where the
    # first column in array is x-values and following next columns are
    y values. If no x values exist, insert column np.arange(len(arr))
    as x values.
    Accepts linear or log x-values, and new x_limits.
    k and s are degree and smoothing factor of the interpolation spline.
    '''
    # first, check whether array should be resampled using
    # a linear or log scale:
    if vec_scale == 'lin':
        new_scale = np.linspace
    if vec_scale == 'log':
        new_scale = np.geomspace
    # get new x-limits for the resampled array
    if new_xlims is None:
        new_x1, new_x2 = arr[0, 0], arr[-1, 0]
    else:
        new_x1, new_x2 = new_xlims[0], new_xlims[1]
    # create new x values
    arrx = new_scale(new_x1, new_x2, new_len)
    # create new empty array to hold resampled values
    stretched_array = np.zeros((new_len, len(arr[0])))
    stretched_array[:, 0] = arrx 
    # for each y-column, calculate parameters of degree-3 spline fit
    for col in range(1, len(arr[0])):
        spline_params = splrep(arr[:, 0], arr[:, col], k=int(k), s=s)
        # calculate spline at new x values
        arry = splev(arrx, spline_params)
        # populate stretched data into resampled array
        stretched_array[:, col] = arry
    return stretched_array


def normalize_df(df):
    '''
    Normalize a Pandas Dataframe by looping over each column and setting the
    range of the column from 0 - 1. This function does NOT normalize the first
    column, which is assumed to be the independent variable.
    '''
    # loop over each column
    for i in range(1, len(list(df))):
        # subtract the minimum value
        df.iloc[:, i] -= df.iloc[:, i].min()
        # divide the maximum value
        df.iloc[:, i] /= df.iloc[:, i].max()
    return df

# set new length of resampled spectra
new_length = 500

# dictionary to hold resampled data
all_dfs = {}

# loop over each data set
for df_name in raw_dfs:

    # get the original dataframe
    dfo = raw_dfs[df_name]

    # resample the data
    resampled_data = arr_resample(dfo.values, new_len=new_length)

    # save resampled spectra into a dataframe
    df = pd.DataFrame(columns=dfo.columns, data=resampled_data)

    # normalize spectra using our custom function
    df = normalize_df(df)

    # save resampled dataframe into dictionary
    all_dfs[df_name] = df
    print(df_name.upper()+' original shape: %s' %str(dfo.shape))
    print(df_name.upper()+' new shape: %s' %str(df.shape))

    # plot original data
    p = plot_line(df, title=df_name.upper(),
                  xlabel=dfo.columns[0], ylabel='intensity')

    # plot the resampled spectra
    for i in range(1, len(list(df))):
        p.line(df.iloc[:, 0], df.iloc[:, i], line_color='black',
                legend='spline', alpha=0.4, line_width=1)
    show(p)

FTIR original shape: (1867, 7)
FTIR new shape: (500, 7)


RAMAN original shape: (5220, 7)
RAMAN new shape: (500, 7)


UVVIS original shape: (1801, 7)
UVVIS new shape: (500, 7)


### Format for PCA

To perform PCA on the spectra, we need them transposed, so that each row
corresponds to a day, and each column is a feature
(intensity at a specific wavelength).

In [0]:
# create dictionary to hold transposed datasets
dfs_wide = {}

# loop over each dataset
for df_name in all_dfs:
    df = all_dfs[df_name]
    # get wavelengths
    w = np.array([round(w0, 2) for w0 in df['w'].values]).astype(str)
    # drop wavelength column
    df = df.drop('w', axis=1).transpose().reset_index()
    # reformat day column
    df['index'] = [d.split('day')[1] for d in df['index']]
    # rename day column
    df = df.rename(columns = {'index':'day'})
    # rename headers to be wavelengths
    df.columns = np.insert(w, 0, 'day')
    # save the transposed data tothe dictionary
    dfs_wide[df_name] = df
    print(df_name.upper())
    print(df.head())

FTIR
  day     399.2    406.41    413.63  ...   3976.17   3983.39    3990.6   3997.81
0   1  0.761845  0.763043  0.793882  ...  0.000723  0.000389  0.000622  0.000000
1   2  0.746682  0.729213  0.737296  ...  0.002091  0.001763  0.001696  0.002457
2   3  0.744975  0.740483  0.756666  ...  0.001720  0.001512  0.001743  0.001840
3   4  0.766669  0.779054  0.789793  ...  0.040226  0.040124  0.040479  0.040635
4   5  0.859982  0.872606  0.876290  ...  0.001144  0.000903  0.000523  0.000946

[5 rows x 501 columns]
RAMAN
  day     99.42    107.23    115.05  ...   3976.02   3983.83   3991.65   3999.46
0   1  0.437997  0.505628  0.587729  ...  0.010596  0.015227  0.008327  0.014419
1   2  0.082110  0.111345  0.111388  ...  0.009820  0.012901  0.017395  0.012863
2   3  0.261488  0.332450  0.370534  ...  0.011906  0.005301  0.011623  0.015320
3   4  0.623404  0.770383  0.824580  ...  0.000000  0.011039  0.040148  0.013771
4   5  0.446485  0.564858  0.649239  ...  0.012289  0.012255  0.004613  0.

### Run PCA

Now that the data is normalized and organized by
day, we create input data for the model **X** and target data for the
model **y**. Here **X**are the intensities of optical spectra, and **y** is
the day the spectra were measured on.

In [0]:
from sklearn.decomposition import PCA 

model = PCA(n_components=5, random_state=0)

# array to hold explained variance
explained_var = np.empty((model.n_components, len(dfs_wide)))

# loop over each dataset
for df_i, df_name in enumerate(dfs_wide):
    df = dfs_wide[df_name]

    # define model input
    X = df[df.columns[1:]].values
    # define model targets
    y = df['day'].values
    target_names = df['day'].values.astype(str)

    # fit model
    X_fit = model.fit(X).transform(X)
    #dic_pca[df_name] = pd.DataFrame(data=X_fit, columns=list(df)[1:])
    explained_var0 = model.explained_variance_ratio_
    explained_var[:, df_i] = explained_var0
    print('\n%s - Explained variance per component:' %df_name.upper())
    print(explained_var0) 


    # set up figure to make plot
    p = setup_fig(
        title=df_name.upper()+' PCA-transformed data: milk separated by day',
        xlabel='PC-1',
        ylabel='PC-2')
    colors = ['navy', 'red', 'green', 'yellow', 'gray', 'cyan']

    # loop over each transformed point and plot it         
    for i in range(len(X)):
        day = df['day'].iloc[i]
        p.scatter(X[i, 0], X[i, 1],
                fill_color=colors[int(day)-1],
                alpha=0.6, legend=str(day), size=10)
    output_notebook()
    show(p)



print('\n')
# set up figure to make plot
p = setup_fig(
    title='Explained variance by dataset',
    xlabel='Component',
    ylabel='Explained variance (%)')
colors = ['navy', 'red', 'green']
# plot explained variance for each dataset
for i in range(len(explained_var[0])):
    p.line(np.arange(len(explained_var))+1, explained_var[:, i],
            line_color=colors[i], alpha=0.6, line_width=3,
            legend=list(dfs_wide.keys())[i])
    p.scatter(np.arange(len(explained_var))+1, explained_var[:, i],
            color=colors[i], size=6,
            legend=list(dfs_wide.keys())[i])
output_notebook()
show(p)


FTIR - Explained variance per component:
[0.7895506  0.11287833 0.06458852 0.02811445 0.0048681 ]



RAMAN - Explained variance per component:
[0.96601826 0.01693351 0.00798269 0.00518513 0.00388041]



UVVIS - Explained variance per component:
[0.92009401 0.05361042 0.02301559 0.0019174  0.00136257]


### Define custom functions for multiple peak fitting and peak detection

In [0]:
def multigauss(signal, *params):
    '''
    Function for fitting a signal with multiple gaussian peaks.
    '''
    y = np.zeros_like(signal)
    # for each gauss peak get the center, amplitude, and width
    for i in range(0, len(params), 3):
        ctr = params[i]
        amp = params[i+1]
        wid = params[i+2]
        y = y + amp * np.exp( -((signal - ctr)/wid)**2)
    # return the sum of all the peaks   
    return y


def get_spline(x, y, k=3, s=10):
    '''
    Get the spline fit for a curve using X and Y data.
    k is the order of the spline fit, s is the smoothing parameter.
    '''
    from scipy.interpolate import splrep, splev
    # calculate spline parameters
    spline_params = splrep(x, y, k=k, s=s)
    # create the spline curve
    spline = splev(x, spline_params)
    return spline


def get_savgol(signal, window=21, order=3, deriv=0):
    '''
    Perform Savitzky Golay filtering to a signal using a specified window
    length (must be an odd integer) and polynomial order.
    deriv specifies the derivative to return, where deriv=0 is no derivative.
    '''
    from scipy.signal import savgol_filter
    savgol = savgol_filter(signal,
                           window_length=window,
                           polyorder=order,
                           deriv=deriv)
    return savgol


def get_peaks(x, y, n=3, antipeaks=False):
    '''
    Get x and y values of peaks in a vector. n parameter specifies
    how many points on each side of the peak should be strictly
    increasing/decreasing in order for it to be considered a peak.
    Set antipeaks=True to find antipeaks (dips or troughs) instead of peaks.
    '''
    peaks = []
    for i in range(n, len(x)-n):
        # differences between points at rising and falling edges of peak
        rising_diff = np.diff(y[i-n:i+1])
        falling_diff = np.diff(y[i:i+n+1])
        # for peaks, check if rising edge increases and falling edge decreases
        if antipeaks == False:
            if np.all(rising_diff > 0) and np.all(falling_diff < 0):
                peaks.append([x[i], y[i]])
        # for dips, check if rising edge increases and falling edge decreases
        if antipeaks == True:
            if np.all(rising_diff < 0) and np.all(falling_diff > 0):
                peaks.append([x[i], y[i]])
    return np.array(peaks)



def detect_peaks(x, y, window=21, prominence=0.01):
    '''
    Get peaks from a spectrum of x and y values.
    The prominence_visible argument sets the prominence threshold for what
    constitutes a visible peak.
    The prominence_hidden argument sets the prominence threshold for what
    constitutes a hidden peak.
    The hidden argument specifies whether to search for hidden peaks,
    i.e. features which do not create visible peaks in the spectrum,
    but are buried or convoluted by other peaks.
    The window argument specific window length for smoothing the spectrum.
    This must be an odd integer.
    Returns a 2D array of x and y columns which correspond to peak positoins
    and peak heights.
    '''
    from scipy.signal import savgol_filter, find_peaks
    # make sure inputs are array-like
    x, y_norm = np.array(x), np.array(y)
    # normalize the y data
    y_norm -= np.min(y)
    y_norm /= np.max(y)
    # if window length is an even integer, make it odd
    if window % 2 == 0:
        window += 1
    # get 1st derivative of signal
    deriv1 = savgol_filter(y_norm, window_length=window, polyorder=3, deriv=1)
    # get 2nd derivative of signal
    deriv2 = savgol_filter(y_norm, window_length=window, polyorder=3, deriv=2)
    # find indices where 1st derivative is 0
    zero_indices = np.where(np.diff(np.signbit(deriv1)))[0]
    # select only idices where 2nd derivative < 0
    peak_ind = [i for i in zero_indices if deriv2[i] < 0]
    # find troughs in 2nd derivative, which may correspond to hidden peaks
    hidden_ind = find_peaks(-deriv2, prominence=prominence)[0]
    peak_ind.extend(hidden_ind)
    peaks = np.stack((x[peak_ind], y[peak_ind]), axis=1)
    return peaks

### Automatically detect peaks in spectra

In [0]:
# dictionary for holding peak information
detected_peaks = {}

# loop over each data set
for df_name in all_dfs:
    df = all_dfs[df_name]

    # loop over each spectrum in data set
    for col in df.columns[1:]:

        # smooth the spectrum using a spline fit to reduce noise
        spec = get_savgol(df[col], window=11)

        # detect peaks in the spectrum
        peaks = detect_peaks(df.iloc[:,0], spec, prominence=0.005)
        detected_peaks[df_name+'__'+col] = peaks

        # set up the plot
        p = setup_fig(
            title=df_name.upper()+' '+col+': '+str(len(peaks))+' peaks found',
            xlabel='W', ylabel='Intensity')
        
        # plot the raw spectrum
        p.line(df.iloc[:, 0], df[col], legend='raw', color='blue',
               line_width=4, alpha=0.3)

        # plot the smoothed spectrum
        p.line(df.iloc[:, 0], spec, color='black', line_width=1,
               legend='smooothed')
        
        # plot the detected peaks
        p.cross(peaks[:, 0], peaks[:, 1], size=20, legend='detected peak',
                    fill_color='red', fill_alpha=0.3, line_color='red')
        show(p)

### Fit each spectra to multiple peaks

Now that peaks have been detected in each spectrum, we attempt to fit the
specturm using a multiple Gauss fit using the detected peaks as
the starting guess.

In [0]:
# for curve fitting, import curve_fit
from scipy.optimize import curve_fit

# loop over measurement type
for df_name in all_dfs:
    # loop over each spectrum in data set
    for col in all_dfs[df_name].columns[1:]:

        # set x-value for the fitting to be the wavelength/wavenumber
        x = all_dfs[df_name].iloc[:, 0]
        # smooth the spectrum to reduce noise and use as y-value
        y = get_savgol(all_dfs[df_name][col], window=31)

        # get location of detected each peak
        peak_locs = detected_peaks[df_name+'__'+col]

        # create a guess, and high and low bounds for fitting for each
        # detected peak of the form [center, amplitude, width]
        guess = np.array([])
        lowbounds = np.array([])
        highbounds = np.array([])
        # create guess for each detected peak
        for i in peak_locs:
            guess = np.append(guess, [i[0], i[1], 1000])
            lowbounds = np.append(lowbounds, [0, 0, 0])
            highbounds = np.append(highbounds,
                                   [np.max(x),
                                    1+np.max(y),
                                    np.max(x)])

        # fit the spectrum to multi-peak fit
        popt, _ = curve_fit(multigauss, x, y, p0=guess,
                            bounds=(lowbounds, highbounds))
        # print peak parameters
        param_arr = np.reshape(popt, ((-1, 3)))
        for params_i, params0 in enumerate(param_arr):
            print('peak #%i [center, amplitude, width]:' %params_i)
            print(params0)

        # set up the plot
        p = setup_fig(
            title=df_name.upper()+' '+col+' multi-Gaussian fit',
            xlabel='W', ylabel='Intensity')

        # plot the measured spectrum
        p.line(x, y, legend='measured', color='blue',
               line_width=4, alpha=0.4)

        # loop over each fitted peak and plot it
        for p0 in range(0, len(popt), 3):
            peak0 = multigauss(x, popt[p0+0], popt[p0+1], popt[p0+2])
            p.line(x, peak0, color='green', line_width=1,
                   alpha=1, legend='gauss fit')

        # plot total spectum fit
        tot_spec_fit = multigauss(x, *popt)
        p.line(x, tot_spec_fit, legend='total fit',
               line_width=2, color='black')
        
        show(p)

peak #0 [center, amplitude, width]:
[1.47923704e+03 2.49692635e-01 2.62649917e+02]
peak #1 [center, amplitude, width]:
[1.08462306e+03 2.70146857e-01 1.97009647e+02]
peak #2 [center, amplitude, width]:
[493.27921272   0.86723662 245.95388762]
peak #3 [center, amplitude, width]:
[8.51339946e+02 5.68353513e-02 9.44777497e+01]
peak #4 [center, amplitude, width]:
[7.20864100e+02 4.80857451e-01 1.62645111e+02]
peak #5 [center, amplitude, width]:
[1.63690965e+03 3.17564958e-01 8.26696984e+01]
peak #6 [center, amplitude, width]:
[2.90494619e+03 1.32038159e-01 8.07361448e+01]
peak #7 [center, amplitude, width]:
[2.68996033e+03 4.82752703e-02 2.85800480e+02]
peak #8 [center, amplitude, width]:
[3.31565726e+03 8.97318126e-01 2.44490119e+02]
peak #9 [center, amplitude, width]:
[2.17788056e+03 6.72190511e-02 2.39748706e+02]


peak #0 [center, amplitude, width]:
[7.22628267e+02 2.08450338e-01 1.37210264e+02]
peak #1 [center, amplitude, width]:
[1.21356244e+03 1.83716285e-01 4.29800761e+02]
peak #2 [center, amplitude, width]:
[520.24224422   0.84516862 295.74428583]
peak #3 [center, amplitude, width]:
[1.63158426e+03 3.39385965e-01 8.26671200e+01]
peak #4 [center, amplitude, width]:
[3.28768862e+03 9.87347218e-01 2.24174711e+02]
peak #5 [center, amplitude, width]:
[2.58469710e+03 4.49095304e-02 7.57539095e+02]
peak #6 [center, amplitude, width]:
[3.49537148e+03 1.76704037e-01 1.32628759e+02]
peak #7 [center, amplitude, width]:
[2.47567205e+03 8.67258313e-04 4.15409317e-02]


peak #0 [center, amplitude, width]:
[8.00352872e+02 1.68781967e-01 1.00298671e+02]
peak #1 [center, amplitude, width]:
[6.76332094e+02 4.71036793e-01 1.40319035e+02]
peak #2 [center, amplitude, width]:
[464.68533034   0.76179017 214.14161909]
peak #3 [center, amplitude, width]:
[1.14222445e+03 2.55578026e-01 4.71486601e+02]
peak #4 [center, amplitude, width]:
[1.63375286e+03 3.80078266e-01 9.09235484e+01]
peak #5 [center, amplitude, width]:
[2.73166595e+03 4.75775124e-02 3.76123004e+02]
peak #6 [center, amplitude, width]:
[3.46346267e+03 4.33241606e-01 1.56226771e+02]
peak #7 [center, amplitude, width]:
[2.91810069e+03 1.20552698e-01 9.54322736e+01]
peak #8 [center, amplitude, width]:
[3.26202352e+03 8.90603568e-01 1.99274757e+02]
peak #9 [center, amplitude, width]:
[3.98977892e+03 4.20131370e-39 7.10649648e+02]
peak #10 [center, amplitude, width]:
[2.18806961e+03 5.29424137e-02 1.75751192e+02]


peak #0 [center, amplitude, width]:
[1.08178105e+03 1.20401980e-01 1.26774249e+02]
peak #1 [center, amplitude, width]:
[7.23799770e+02 4.19537628e-01 1.88888505e+02]
peak #2 [center, amplitude, width]:
[458.3406118    0.78335875 275.72358019]
peak #3 [center, amplitude, width]:
[1.39338745e+03 1.38153897e-01 2.45825204e+02]
peak #4 [center, amplitude, width]:
[1.63810250e+03 3.30939489e-01 8.20829701e+01]
peak #5 [center, amplitude, width]:
[3.24625429e+03 8.37699894e-01 1.84815531e+02]
peak #6 [center, amplitude, width]:
[2.91814238e+03 7.37712715e-02 1.12834929e+02]
peak #7 [center, amplitude, width]:
[3.19720513e+03 4.52919985e-02 1.15098689e+03]
peak #8 [center, amplitude, width]:
[3.45368471e+03 4.94743827e-01 1.62588670e+02]
peak #9 [center, amplitude, width]:
[2.17597038e+03 3.37616947e-02 1.45925187e+02]


peak #0 [center, amplitude, width]:
[490.71547769   0.92633411 288.16291471]
peak #1 [center, amplitude, width]:
[7.19902367e+02 2.61638962e-01 1.47018311e+02]
peak #2 [center, amplitude, width]:
[1.20471785e+03 1.77197651e-01 4.70880841e+02]
peak #3 [center, amplitude, width]:
[1.63346913e+03 3.33168755e-01 8.28220991e+01]
peak #4 [center, amplitude, width]:
[2.92293911e+03 7.07132342e-02 1.09928978e+02]
peak #5 [center, amplitude, width]:
[3.24383657e+03 8.71507953e-01 1.84400558e+02]
peak #6 [center, amplitude, width]:
[3.44960794e+03 5.03246420e-01 1.65127120e+02]
peak #7 [center, amplitude, width]:
[2.72267239e+03 3.15586695e-02 3.74412342e+02]
peak #8 [center, amplitude, width]:
[2.17462581e+03 5.05741971e-02 1.85160743e+02]


...

peak #0 [center, amplitude, width]:
[1.26146444e+02 2.56808377e-39 6.51837330e+02]
peak #1 [center, amplitude, width]:
[357.98908257   0.61455393  69.02187938]
peak #2 [center, amplitude, width]:
[481.12148674   0.73139166 129.75987251]
peak #3 [center, amplitude, width]:
[1.04079741e+03 6.80931476e-01 3.14185511e+02]
peak #4 [center, amplitude, width]:
[7.09656718e+02 7.07264235e-01 2.02934356e+02]
peak #5 [center, amplitude, width]:
[1.01597131e+03 5.04266493e-35 3.48758547e+02]
peak #6 [center, amplitude, width]:
[1.59822894e+03 1.30388315e-01 8.01450396e+01]
peak #7 [center, amplitude, width]:
[1.83534096e+03 3.28468842e-02 4.91713911e+01]
peak #8 [center, amplitude, width]:
[1.76146556e+03 9.83317281e-02 1.05704615e+02]
peak #9 [center, amplitude, width]:
[1.99817255e+03 7.69823229e-02 1.55158631e+02]
peak #10 [center, amplitude, width]:
[9.76139194e+02 1.12391296e-30 3.45716023e+02]


peak #0 [center, amplitude, width]:
[4.37264850e+01 6.04765207e-44 6.45215920e+02]
peak #1 [center, amplitude, width]:
[359.04756727   0.65890743  70.24597631]
peak #2 [center, amplitude, width]:
[491.8151787    0.76590755 132.3469723 ]
peak #3 [center, amplitude, width]:
[1.03050939e+03 6.89494774e-01 3.19302998e+02]
peak #4 [center, amplitude, width]:
[9.99125308e+02 1.55035053e-07 3.05787339e+02]
peak #5 [center, amplitude, width]:
[7.18510131e+02 6.57417803e-01 1.87962433e+02]
peak #6 [center, amplitude, width]:
[1.60418687e+03 1.32447401e-01 8.43438525e+01]
peak #7 [center, amplitude, width]:
[1.78186963e+03 9.49523914e-02 9.89184747e+01]
peak #8 [center, amplitude, width]:
[1.98464560e+03 7.04201601e-02 1.91584318e+02]
peak #9 [center, amplitude, width]:
[1.78666357e+03 8.81663544e-20 1.40402445e+02]
peak #10 [center, amplitude, width]:
[7.37754405e+02 2.63818442e-45 5.66439963e+02]


peak #0 [center, amplitude, width]:
[9.43311729e+02 8.09904763e-33 4.27136656e+02]
peak #1 [center, amplitude, width]:
[360.31348508   0.61362771  68.76559936]
peak #2 [center, amplitude, width]:
[3.57766230e+02 1.11943523e+00 1.43901020e-01]
peak #3 [center, amplitude, width]:
[492.48239829   0.64422633 138.54368418]
peak #4 [center, amplitude, width]:
[1.27045434e+03 4.24529008e-01 9.84527185e+01]
peak #5 [center, amplitude, width]:
[797.91683118   0.97337995 286.89251998]
peak #6 [center, amplitude, width]:
[1.58876599e+03 1.53938842e-01 1.63555711e+02]
peak #7 [center, amplitude, width]:
[1.94605105e+03 1.67782989e-37 2.13234201e+02]
peak #8 [center, amplitude, width]:
[1.81577731e+03 9.19475601e-02 7.92104748e+01]
peak #9 [center, amplitude, width]:
[1.99864261e+03 7.58806208e-02 1.24869546e+02]
peak #10 [center, amplitude, width]:
[1.08425291e+03 4.46246689e-01 7.03860890e+01]


peak #0 [center, amplitude, width]:
[9.18898505e+02 1.41332710e-01 6.09431234e+01]
peak #1 [center, amplitude, width]:
[328.0742608    0.34793231  45.56219442]
peak #2 [center, amplitude, width]:
[383.94172822   0.51125224  66.21984436]
peak #3 [center, amplitude, width]:
[497.80399569   0.63884135 129.88912398]
peak #4 [center, amplitude, width]:
[1.26750032e+03 4.65262833e-01 9.74160527e+01]
peak #5 [center, amplitude, width]:
[1.07968148e+03 5.86825112e-01 8.31218312e+01]
peak #6 [center, amplitude, width]:
[1.61608772e+03 3.70414916e-02 4.63075067e+01]
peak #7 [center, amplitude, width]:
[1.99707129e+03 6.91711375e-02 7.62093387e+01]
peak #8 [center, amplitude, width]:
[1.56610429e+03 1.32671151e-01 1.70990267e+02]
peak #9 [center, amplitude, width]:
[1.81942258e+03 1.03187914e-01 1.03748623e+02]
peak #10 [center, amplitude, width]:
[771.96994056   0.96703217 254.79239601]


peak #0 [center, amplitude, width]:
[9.79374949e+01 8.08368695e-36 5.47028645e+02]
peak #1 [center, amplitude, width]:
[493.12805171   0.78319891 133.09814946]
peak #2 [center, amplitude, width]:
[358.96298547   0.6606039   69.83452431]
peak #3 [center, amplitude, width]:
[7.20944354e+02 6.09069403e-01 1.80449355e+02]
peak #4 [center, amplitude, width]:
[1.62284008e+03 5.18084819e-36 7.29122796e+02]
peak #5 [center, amplitude, width]:
[1.01915281e+03 6.91104870e-01 3.32320266e+02]
peak #6 [center, amplitude, width]:
[1.59600034e+03 1.21297081e-01 8.43551345e+01]
peak #7 [center, amplitude, width]:
[1.99973990e+03 6.79706643e-02 6.51069497e+01]
peak #8 [center, amplitude, width]:
[1.90531635e+03 4.37200839e-35 2.63042560e+02]
peak #9 [center, amplitude, width]:
[1.80451627e+03 1.26346313e-01 1.44120826e+02]
peak #10 [center, amplitude, width]:
[1.05802106e+03 9.47407927e-40 4.84694937e+02]
